In [0]:
file = {"namespace":"/oni","type_raw":"/usr", "file_folder":"/mte/rais", "file_subfolder":"/rais_estabelecimentos_2018_2023", "prm_path": "/prm/usr/me/KC2332_ME_RAIS_ESTABELECIMENTO_mapeamento_raw.xlsx", "extension":"txt","column_delimiter":"","encoding":"","null_value":""}

adf = { "adf_factory_name": "cnibigdatafactory", "adf_pipeline_name": "raw_trs_tb_email", "adf_pipeline_run_id": "61fc4f3c-c592-426d-bb36-c85cb184bb82", "adf_trigger_id": "92abb4ec-2b1f-44e0-8245-7bc165f91016", "adf_trigger_name": "92abb4ec-2b1f-44e0-8245-7bc165f91016", "adf_trigger_time": "2024-05-07T00:58:48.0960873Z", "adf_trigger_type": "PipelineActivity" }

dls = { "folders": { "landing": "/tmp/dev/uld", "error": "/tmp/dev/err", "staging": "/tmp/dev/stg", "log": "/tmp/dev/log", "raw": "/tmp/dev/raw", "archive": "/tmp/dev/ach" }, "systems": { "raw": "usr" }, "path_prefix": "" }

dbutils.widgets.text("user_parameters", '{"null": "null"}')

dbutils.widgets.text("env", 'dev')

dbutils.widgets.text("storage", '{"url": "https://cnibigdatadlsgen2.dfs.core.windows.net", "container": "datalake"}')

In [0]:
# Biblioteca cni_connectors, que dá acesso aos dados no datalake
from cni_connectors import adls_connector as adls_conn

# A biblioteca criada para facilitar a declaração dos testes. É necessário importá-la.
### from datatest.gx_context_provider import GXContextProvider

# Essa declaração é necessária em todos os notebooks. Somente através dela podemos acessar os dados no datalake.
var_adls_uri, notebook_params = adls_conn.connect_adls()

from pyspark.sql.functions import udf, from_utc_timestamp, current_timestamp, lit, input_file_name, monotonically_increasing_id, substring_index
from trs_control_field import trs_control_field as tcf
import pyspark.sql.functions as f
import crawler.functions as cf
from pyspark.sql import SparkSession
import time
import pandas as pd
from pyspark.sql.functions import col, when, explode, lit
import json
from unicodedata import normalize 
import datetime
import re
from core.string_utils import normalize_replace
from pyspark.sql.functions import concat, lit, col

In [0]:
# Esses são os dicionários de configuração da transformação enviados pelo ADF e acessados via widgets. Os diretórios de origem e destino das tabelas são compostos por valores em 'dls' e 'tables'.
# Parametros necessario para na ingestão

file = notebook_params.var_file
dls = notebook_params.var_dls
adf = notebook_params.var_adf

In [0]:
uld = dls['folders']['landing']
raw = dls['folders']['raw']
usr = dls['systems']['raw']

In [0]:
uld_path = "{uld}{namespace}{file_folder}{file_subfolder}".format(uld=uld, namespace=tables['namespace'], file_folder=tables['file_folder'], file_subfolder=tables['file_subfolder'])
adl_uld = f"{var_adls_uri}{uld_path}"
adl_uld

Out[6]: 'abfss://datalake@cnibigdatadlsgen2.dfs.core.windows.net/tmp/dev/uld/oni/mte/rais/rais_estabelecimentos_2018_2023'

In [0]:
raw_path = "{raw}{type_raw}{namespace}{file_folder}{file_subfolder}".format(raw=raw, type_raw=tables['type_raw'], namespace=tables['namespace'], file_folder=tables['file_folder'], file_subfolder=tables['file_subfolder'])
adl_raw = f"{var_adls_uri}{raw_path}"
adl_raw

Out[7]: 'abfss://datalake@cnibigdatadlsgen2.dfs.core.windows.net/tmp/dev/raw/usr/oni/mte/rais/rais_estabelecimentos_2018_2023'

In [0]:
# Path sem {var_adls_uri} e cuidado com /tmp/dev
prm_path = "{path_prefix}{prm_path}".format(path_prefix=dls['path_prefix'], prm_path=tables['prm_path'])
prm_path

Out[8]: '/prm/usr/me/KC2332_ME_RAIS_ESTABELECIMENTO_mapeamento_raw.xlsx'

In [0]:
cf.list_adl_files(spark, dbutils, uld_path).display()

nm_arq_in dh_arq_in Estb2018ID.txt 2024-10-16T11:17:18.000+0000 Estb2019ID.txt 2024-10-16T11:17:29.000+0000 Estb2020ID.txt 2024-10-16T16:49:37.000+0000 Estb2021ID.txt 2024-10-16T11:18:07.000+0000 RAIS_ESTAB_ID.txt.txt 2024-10-16T11:18:07.000+0000 RAIS_ESTAB_ID.txt 2024-10-16T11:18:28.000+0000

In [0]:
# Para multiples frames

dataframes = []

for file_path in cf.list_subdirectory(dbutils, uld_path):
    full_path = f"{var_adls_uri}/{file_path}"
    year = file_path.split('/')[-1]

    pattern = r"\d+"
    numbers = re.findall(pattern, year)[0]
    
    df = (spark.read
        .option("delimiter", ";")
        .option("header", "true")
        .option("encoding", "ISO-8859-1")  # Specify the encoding
        .csv(full_path, header=True)
        ).withColumn("ANO", lit(f"{numbers}"))
    dataframes.append(df)  # Store the DataFrame in a list

# Union all DataFrames in the list
combined_df = dataframes[0] if dataframes else spark.createDataFrame([], schema=None)
for df in dataframes[1:]:
    combined_df = combined_df.union(df)

df = combined_df

In [0]:
df.columns

Out[11]: ['CEI Vinculado',
 'CEP Estab',
 'CNAE 95 Classe',
 'CNPJ / CEI',
 'CNPJ Raiz',
 'Data Abertura',
 'Data Baixa',
 'Data Encerramento',
 'Email Estabelecimento',
 'Ind CEI Vinculado',
 'Ind Estab Participa PAT',
 'Ind Rais Negativa',
 'Ind Simples',
 'Município',
 'Natureza Jurídica',
 'Nome Logradouro',
 'Número Logradouro',
 'Nome Bairro',
 'Número Telefone Empresa',
 'Qtd Vínculos Ativos',
 'Qtd Vínculos CLT',
 'Qtd Vínculos Estatutários',
 'Razão Social',
 'Tamanho Estabelecimento',
 'Tipo Estab',
 'IBGE Subsetor',
 'Ind Atividade Ano',
 'CNAE 2.0 Classe',
 'CNAE 2.0 Subclasse',
 'ANO']

In [0]:
def __normalize_str(_str):
    return re.sub(r'[,;{}()\n\t=-]', '', normalize('NFKD', _str)
                  .encode('ASCII', 'ignore')
                  .decode('ASCII')
                  .replace(' ', '_')
                  .replace('-', '_')
                  .replace('/', '_')
                  .replace('.', '_')
                  .replace('$', 'S')
                  .upper())
  
for column in df.columns:
  df = df.withColumnRenamed(column, __normalize_str(column))

In [0]:
df_2018 = df.filter(df.ANO == '2018')
df_2019 = df.filter(df.ANO == '2019')
df_2020 = df.filter(df.ANO == '2020')
df_2021 = df.filter(df.ANO == '2021')
df_2022 = df.filter(df.ANO == '2022')
df_2023 = df.filter(df.ANO == '2023')

In [0]:
# Usou-se sheet_names paenas para 2018, pois ele é compatível com todos
headers = {'name_header':'Campo Origem','pos_header':'C','pos_org':'C','pos_dst':'E','pos_type':'F'}
var_prm_dict = cf.parse_ba_doc(dbutils, prm_path, headers=headers, sheet_names=['2018'])

# var_prm_dict = cf.parse_ba_doc(dbutils, '/tmp/dev/prm/usr/me/KC2332_ME_RAIS_ESTABELECIMENTO_mapeamento_raw.xlsx', headers=headers, sheet_names='2021')
# '/tmp/dev/prm/usr/me/KC2332_ME_RAIS_ESTABELECIMENTO_mapeamento_raw.xlsx'

In [0]:
var_prm_dict

Out[15]: {'2018': [['CEI_VINCULADO', 'ID_CEI_VINCULADO', 'long'],
  ['CEP_ESTAB', 'ID_CEPAO_ESTAB', 'double'],
  ['CNAE_95_CLASSE', 'CD_CNAE10_CLASSE', 'integer'],
  ['CNPJ___CEI', 'ID_CNPJ_CEI', 'string'],
  ['CNPJ_RAIZ', 'ID_CNPJ_RAIZ', 'string'],
  ['DATA_ABERTURA', 'DT_ABERTURA', 'integer'],
  ['DATA_BAIXA', 'DT_BAIXA', 'integer'],
  ['DATA_ENCERRAMENTO', 'DT_ENCERRAMENTO', 'integer'],
  ['EMAIL_ESTABELECIMENTO', 'NM_EMAIL', 'string'],
  ['IND_CEI_VINCULADO', 'FL_IND_CEI_VINCULADO', 'integer'],
  ['IND_ESTAB_PARTICIPA_PAT', 'FL_IND_ESTAB_PARTICIPA_PAT', 'integer'],
  ['IND_RAIS_NEGATIVA', 'FL_IND_RAIS_NEGAT', 'integer'],
  ['IND_SIMPLES', 'FL_IND_SIMPLES', 'integer'],
  ['MUNICIPIO', 'CD_MUNICIPIO', 'integer'],
  ['NATUREZA_JURIDICA', 'CD_NATUREZA_JURIDICA', 'integer'],
  ['NOME_LOGRADOURO', 'NM_LOGRADOURO', 'string'],
  ['NUMERO_LOGRADOURO', 'NR_LOGRADOURO', 'double'],
  ['NOME_BAIRRO', 'NM_BAIRRO', 'string'],
  ['NUMERO_TELEFONE_EMPRESA', 'NR_TELEFONE_EMPRE', 'long'],
  ['QTD_VIN

In [0]:
def __select(parse_ba_doc, year):
  for org, dst, _type in parse_ba_doc[year]:
    if org == 'N/A' and dst not in df.columns:
      yield f.lit(None).cast(_type).alias(dst)
    else:
      _col = f.col(org)
      if _type.lower() == 'double':
        _col = f.regexp_replace(org, ',', '.')
      yield _col.cast(_type).alias(dst)

In [0]:
df_2018 = df_2018.select(*__select(parse_ba_doc=var_prm_dict, year='2018'))
df_2018 = df_2018.withColumn('ANO', f.lit('2018').cast('Int'))

df_2019 = df_2019.select(*__select(parse_ba_doc=var_prm_dict, year='2018'))
df_2019 = df_2019.withColumn('ANO', f.lit('2019').cast('Int'))

df_2020 = df_2020.select(*__select(parse_ba_doc=var_prm_dict, year='2018'))
df_2020 = df_2020.withColumn('ANO', f.lit('2020').cast('Int'))

df_2021 = df_2021.select(*__select(parse_ba_doc=var_prm_dict, year='2018'))
df_2021 = df_2021.withColumn('ANO', f.lit('2021').cast('Int'))

df_2022 = df_2022.select(*__select(parse_ba_doc=var_prm_dict, year='2018'))
df_2022 = df_2022.withColumn('ANO', f.lit('2022').cast('Int'))

df_2023 = df_2023.select(*__select(parse_ba_doc=var_prm_dict, year='2018'))
df_2023 = df_2023.withColumn('ANO', f.lit('2023').cast('Int'))

In [0]:
from functools import reduce

# Step 3: Union All DataFrames
dfs = [df_2018, df_2019, df_2020, df_2021, df_2022, df_2023]
df = reduce(lambda df1, df2: df1.union(df2), dfs)

In [0]:
# #inserção de coluna de ingestão na camada raw
df = cf.append_control_columns(df, dh_insercao_raw=adf["adf_trigger_time"].split(".")[0])
dh_insercao_raw = datetime.datetime.now()
df = df.withColumn('dh_insercao_raw', f.lit(dh_insercao_raw).cast('timestamp'))

df_adl_files = cf.list_adl_files(spark, dbutils, uld_path)
df = df.join(f.broadcast(df_adl_files), on='nm_arq_in', how='inner')

In [0]:
df.filter(df.ANO == '2021').display()

nm_arq_in ID_CEI_VINCULADO ID_CEPAO_ESTAB CD_CNAE10_CLASSE ID_CNPJ_CEI ID_CNPJ_RAIZ DT_ABERTURA DT_BAIXA DT_ENCERRAMENTO NM_EMAIL FL_IND_CEI_VINCULADO FL_IND_ESTAB_PARTICIPA_PAT FL_IND_RAIS_NEGAT FL_IND_SIMPLES CD_MUNICIPIO CD_NATUREZA_JURIDICA NM_LOGRADOURO NR_LOGRADOURO NM_BAIRRO NR_TELEFONE_EMPRE QT_VINC_ATIV QT_VINC_CLT QT_VINC_ESTAT ID_RAZAO_SOCIAL CD_TAMANHO_ESTABELECIMENTO CD_TIPO_ESTAB_ID CD_IBGE_SUBSETOR FL_IND_ATIV_ANO CD_CNAE20_CLASSE CD_CNAE20_SUBCLASSE CD_UF ANO nr_reg dh_insercao_raw dh_arq_in Estb2021ID.txt 0 7.6963754E7 52299 17206609000114 17206609 23112012 0 0 ESC_ELDORADO@HOTMAIL.COM 0 0 0 1 110004 2135 AVENIDA CASTELO BRANCO 19936.0 CENTRO 69034413016 7 7 0 M S SOUZA ME 3 1 16 1 47296 4729699 null 2021 549755813888 2024-10-17T20:37:59.016+0000 2024-10-16T11:18:07.000+0000 Estb2021ID.txt 0 7.6963888E7 52299 17206609000203 17206609 6122012 0 0 ESC_ELDORADO@HOTMAIL.COM 0 0 0 1 110004 2135 AVENIDA PORTO VELHO 2444.0 CENTRO 69034414308 0 0 0 M S SOUZA ME-FILIAL 1 1 16 1 47296 4729699 null 2021 549755813889 2024-10-17T20:37:59.016+0000 2024-10-16T11:18:07.000+0000 Estb2021ID.txt 0 7.6847E7 60267 17207108000152 17207108 23112012 0 0 EXTREMA-CONTABILIDADE@HOTMAIL.COM 0 0 0 1 110020 2135 RUA ABUNA 587.0 EXTREMA 69032522053 1 1 0 ZENIO FERNANDES DE MIRANDA FILHO - ME 2 1 20 1 49302 4930201 null 2021 549755813890 2024-10-17T20:37:59.016+0000 2024-10-16T11:18:07.000+0000 Estb2021ID.txt 0 7.698009E7 52450 17202654000109 17202654 22112012 0 0 THIAGO_MEGACELL@HOTMAIL.COM 0 0 0 1 110030 2135 AVENIDA MAJOR AMARANTE 3570.0 CENTRO 69033224717 0 0 0 THIAGO VINICIUS FERREIRA VICENTINI 00848 1 1 16 1 47521 4752100 null 2021 549755813891 2024-10-17T20:37:59.016+0000 2024-10-16T11:18:07.000+0000 Estb2021ID.txt 0 7.6821013E7 50105 17207413000225 17207413 7102014 0 0 RAVIERA@RAVIERAMOTORS.COM.BR 0 0 0 0 110020 2062 TIRADENTES 3333.0 INDUSTRIAL 68032147000 41 41 0 RAVIERA MOTORS COMERCIAL DE VEICULOS LTDA 5 1 16 1 45111 4511101 null 2021 549755813892 2024-10-17T20:37:59.016+0000 2024-10-16T11:18:07.000+0000 Estb2021ID.txt 0 7.6980002E7 50105 17207413000306 17207413 7012016 0 0 RAVIERAMOTORS@RAVIERAMOTORS.COM.BR 0 0 0 0 110030 2062 CELSO MAZUTTI 8181.0 SETOR INDUSTRIAL 68032147000 18 18 0 RAVIERA MOTORS COMERCIAL DE VEICULOS LTDA 4 1 16 1 45111 4511101 null 2021 549755813893 2024-10-17T20:37:59.016+0000 2024-10-16T11:18:07.000+0000 Estb2021ID.txt 0 7.6900041E7 50105 17207413000497 17207413 3032016 0 0 0 0 0 0 110012 2062 TRANSCONTINENTAL 281.0 CENTRO 68032147000 23 23 0 RAVIERA MOTORS COMERCIAL DE VEICULOS LTDA 5 1 16 1 45111 4511101 null 2021 549755813894 2024-10-17T20:37:59.016+0000 2024-10-16T11:18:07.000+0000 Estb2021ID.txt 0 7.6857E7 74160 18678393000152 18678393 14082013 0 0 CONTEC_CONTAB_@HOTMAIL.COM 0 0 0 0 110033 2135 AVENIDA DEZIDERIO DOMINGOS LOPES 4019.0 CENTRO 69035442733 2 2 0 C. U. O. PINHEIRO DA SILVA - ME 2 1 19 1 74901 7490103 null 2021 549755813895 2024-10-17T20:37:59.016+0000 2024-10-16T11:18:07.000+0000 Estb2021ID.txt 0 7.6900081E7 74993 18650294000162 18650294 8082013 0 0 NEY.CONTADOR.2010@GMAIL.COM 0 0 0 0 110012 2062 AVENIDA MARECHAL RONDON 870.0 CENTRO 69034218747 1 1 0 GSV ASSESSORIA EMPRESARIAL LTDA 2 1 19 1 82113 8211300 null 2021 549755813896 2024-10-17T20:37:59.016+0000 2024-10-16T11:18:07.000+0000 Estb2021ID.txt 0 7.6987076E7 52434 18664696000116 18664696 12082013 0 0 EASSESSORTEC@HOTMAIL.COM 0 0 0 1 110030 2135 RUA LUIZ SERAFIM 527.0 JARDIM ELDORADO 69033228671 1 1 0 K V DA SILVA 2 1 16 1 47598 4759801 null 2021 549755813897 2024-10-17T20:37:59.016+0000 2024-10-16T11:18:07.000+0000 Estb2021ID.txt 0 7.6873416E7 64203 18669690000131 18669690 9082013 0 0 ASSERTCONTABILIDADE@GMAIL.COM 0 0 0 1 110002 2062 ALAMEDA FLOR DO IPE 3033.0 SETOR 04 69035353858 6 6 0 NOVANET MULTIMIDIA LTDA 3 1 20 1 61906 6190601 null 2021 549755813898 2024-10-17T20:37:59.016+0000 2024-10-16T11:18:07.000+0000 Estb2021ID.txt 0 7.6916E7 17493 18701587000121 18701587 19082013 0 0 DECISAOCONTABILIDADE.RO@GMAIL.COM 0 0 0 1 110025 2135 AV 

In [0]:
df.repartition(10).write.partitionBy('ANO').parquet(path=adl_raw, mode='overwrite')

In [0]:

headers = {'name_header':'Campo Origem','pos_header':'C','pos_org':'C','pos_dst':'E','pos_type':'F'}
# var_prm_dict = cf.parse_ba_doc(dbutils, '/tmp/dev/prm/usr/me/KC2332_ME_RAIS_ESTABELECIMENTO_mapeamento_raw.xlsx', headers=headers, sheet_names='2021')
var_prm_dict = cf.parse_ba_doc(dbutils, '/prm/usr/me/KC2332_ME_RAIS_ESTABELECIMENTO_mapeamento_raw.xlsx', headers=headers, sheet_names=['2018', '2019', '2020','2021','2022','2023'])
# '/tmp/dev/prm/usr/me/KC2332_ME_RAIS_ESTABELECIMENTO_mapeamento_raw.xlsx'

In [0]:
# Para multiples frames

dataframes = []

for file_path in cf.list_subdirectory(dbutils, uld_path):
    full_path = f"{var_adls_uri}/{file_path}"
    year = file_path.split('/')[-1]

    pattern = r"\d+"
    numbers = re.findall(pattern, year)[0]
    
    df = (spark.read
        .option("delimiter", ";")
        .option("header", "true")
        .option("encoding", "ISO-8859-1")  # Specify the encoding
        .csv(full_path, header=True)
        ).withColumn("ANO", lit(f"{numbers}"))
    dataframes.append(df)  # Store the DataFrame in a list

# Union all DataFrames in the list
combined_df = dataframes[0] if dataframes else spark.createDataFrame([], schema=None)
for df in dataframes[1:]:
    combined_df = combined_df.union(df)

df = combined_df

In [0]:
# Adição da coluna de controle de data de ingestão

dt_insertion_raw = adf['adf_trigger_time'].split('.')[0]
df = cf.append_control_columns(df, dt_insertion_raw)

In [0]:
# Join com coluna inner com nome dos arquivos

adl_file_time = cf.list_adl_files(spark, dbutils, uld_path)
df = df.join(adl_file_time, on='nm_arq_in', how='inner')

In [0]:
# Matching PRM


var_prm_dict = cf.parse_ba_doc_spark(dbutils, var_file_prm, headers=headers, sheet_names=var_year)

headers = {'name_header':'Campo Origem','pos_header':'C','pos_org':'C','pos_dst':'E','pos_type':'F'}

parse_ba_doc = cf.parse_ba_doc(dbutils, prm_path, headers=headers, sheet_names=[var_year])
cf.check_ba_doc(df, parse_ba=parse_ba_doc, sheet=var_year)


def __select(parse_ba_doc, year):
  for org, dst, _type in parse_ba_doc[year]:
    if org == 'N/A' and dst not in df.columns:
      yield f.lit(None).cast(_type).alias(dst)
    else:
      _col = f.col(org)
      if _type.lower() == 'double':
        _col = f.regexp_replace(org, ',', '.')
      yield _col.cast(_type).alias(dst)
      
df = df.select(*__select(parse_ba_doc=parse_ba_doc, year='2018'))



# Outra forma de __transform_columns 

def __transform_columns(var_prm_dict__sheet_name: dict):
  for org, dst, _type in var_prm_dict__sheet_name:
    if org == 'N/A':
      yield f.lit(None).cast(_type).alias(dst)
    else:
      yield f.col(org).cast(_type).alias(dst)

dh_insercao_raw = adf['adf_trigger_time']
if dh_insercao_raw is not None:
  dh_insercao_raw = dh_insercao_raw.split(".")[0]

df_adl_files = cf.list_adl_files(spark, dbutils, uld_path)

In [0]:
# Nova função parse_ba_doc_spar
# var_prm_dict = []
# headers = {'name_header':'Campo Origem','pos_header':'C','pos_org':'C','pos_dst':'E','pos_type':'F'}
# var_prm_dict = cf.parse_ba_doc_spark(dbutils, var_file_prm, headers=headers, sheet_names=var_year)

In [0]:
# Para 2 sparkframe
# for file_path in cf.list_subdirectory(dbutils, uld_path):
#   full_path = f"{var_adls_uri}/{file_path}"
#   year = file_path.split('/')[-1]

#  pattern = r"\d+"
#  numbers = re.findall(pattern, year)[0]
#  print(numbers)
#  df = (spark.read
#      .option("delimiter", ";")
#      .option("header", "true")
#      .option("charset", "UTF-8")  # Specify the encoding
#      .csv(full_path, header=True)
#     ).withColumn("ANO", lit(f"{numbers}"))
#  combined_df = spark.createDataFrame([], df.schema)
#    # Concatenate the DataFrame
#  combined_df = combined_df.union(df)

In [0]:
Example code to union multiple DataFrames

import re
from pyspark.sql import SparkSession
from pyspark.sql.functions import lit

# Initialize Spark session
spark = SparkSession.builder.appName("UnionDataFrames").getOrCreate()

# Simulated list of file paths (normally obtained from a directory listing)
file_paths = [
    "2021_sales.csv",
    "2022_sales.csv",
    "2023_sales.csv"
]

# List to hold DataFrames
dataframes = []

# Loop through each file path
for file_path in file_paths:
    # Simulating full path (adjust the base path as needed)
    full_path = f"/path/to/your/data/{file_path}"
    year = file_path.split('_')[0]  # Extract year from the file name

    # Extract the year using regex
    pattern = r"\d+"
    numbers = re.findall(pattern, year)[0]

    # Read the CSV file and add a new column for the year
    df = (spark.read.option("delimiter", ";").csv(full_path, header=True)).withColumn("ANO", lit(numbers))
    
    # Append the DataFrame to the list
    dataframes.append(df)

# Union all DataFrames in the list
if dataframes:  # Check if the list is not empty
    combined_df = dataframes[0]  # Start with the first DataFrame
    for df in dataframes[1:]:  # Union the rest
        combined_df = combined_df.union(df)
else:
    combined_df = spark.createDataFrame([], schema=None)  # Create an empty DataFrame if no files

# Show the combined DataFrame
combined_df.show()